In [ ]:
%load_ext autoreload
%autoreload 1
# %aimport ...

In [1]:
from robotodo.engines.isaac._kernel import Kernel

In [ ]:
# kernel = KernelThread(["--/app/asyncRendering=True"])
kernel = Kernel(
    [
        # "--no-window",
        # "--/app/window/hideUi=true",
        # "--/app/asyncRendering=true",
        # TODO
        # "--enable", "omni.services.streamclient.webrtc",
    ]
)

[Warning] [simulation_app] Interactive python shell detected but ISAAC_JUPYTER_KERNEL was not set. Problems with asyncio may occur
[Warning] [simulation_app] Please use Isaac Sim Python 3 kernel instead of the default Python 3 Kernel
Loading user config located at: '/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/omni/data/Kit/Isaac-Sim Full/5.0/user.config.json'
2025-09-12T09:13:21Z s] [Warning] [omni.kit.app.plugin] No crash reporter present, dumps uploading isn't available.
[0.085s] [ext: omni.kit.async_engine-0.0.3] startup
[0.324s] [ext: omni.metrics.core-0.0.3] startup
[0.324s] [ext: omni.client.lib-1.1.0] startup
[0.340s] [ext: omni.blobkey-1.1.2] startup
[0.341s] [ext: omni.stats-1.0.1] startup
[0.342s] [ext: omni.datastore-0.0.0] startup
[0.350s] [ext: omni.client-1.3.0] startup
[0.406s] [ext: omni.ujitso.default-1.0.0] startup
[0.410s] [ext: omni.hsscclient-1.1.2] startup
[0.417s] [ext: omni.gpu_foundation.shadercache.vulkan-1.0.0] startup
[0.419s] [ext: omni.

Checking to see if RMW can be loaded:
failed to get symbol 'rmw_init_options_init' due to Environment variable 'AMENT_PREFIX_PATH' is not set or empty, at /workspace/humble_ws/src/rmw_implementation/src/functions.cpp:171, at /workspace/humble_ws/src/rcl/rcl/src/rcl/init_options.c:75
RMW was not loaded

TODO <pxr.Usd.ObjectsChanged object at 0x7f8db061c180> Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('anon:0x7f9c78011910:World0-session.usda'), pathResolverContext=<invalid repr>)
TODO <pxr.Usd.ObjectsChanged object at 0x7f8db061fb00> Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('anon:0x7f9c78011910:World0-session.usda'), pathResolverContext=<invalid repr>)


In [ ]:
from typing import TypedDict

import numpy
import scipy.spatial.transform
import einops


# TODO
class ProtoPose(TypedDict):
    pass


# TODO support (*batch_dims, data)
# TODO dataclass???
# TODO testing
# TODO from/to 4x4 trans matrix !!!!!!
class Pose(dict):
    p: ...  # TODO xyz
    q: ...  # TODO xyzw
    # angles: ... # TODO radian xyz

    @classmethod
    def from_matrix(cls, matrix):
        # TODO !!!!
        matrix = numpy.asarray(matrix)
        return Pose(
            p=matrix[..., :3, 3],
            q=scipy.spatial.transform.Rotation.from_matrix(matrix[..., :3, :3]).as_quat(),
        )

    def __init__(
        self,
        # TODO
        # other: ProtoPose,
        *,
        p: ... = [0, 0, 0],
        q: ... = [0, 0, 0, 1],
        # angles: ... = [0, 0, 0],
    ):
        super().__init__(p=p, q=q)

    # TODO better ux!!!
    def _todo_get(self, *index):
        return Pose(
            p=self["p"][*index, :],
            q=self["q"][*index, :],
        )

    # TODO
    def facing(self, pose: "Pose"):
        # TODO
        raise NotImplementedError

    def rotated(self, angles):
        # raise NotImplementedError
        # TODO
        return Pose(
            p=self["p"],
            q=(
                scipy.spatial.transform.Rotation.from_quat(self["q"])
                * scipy.spatial.transform.Rotation.from_euler("XYZ", angles)
            ).as_quat(),
        )

    def translated(self, positions):
        raise NotImplementedError

    # TODO FIXME performance
    def inv(self):
        rot_inv = scipy.spatial.transform.Rotation.from_quat(self["q"]).inv()
        return Pose(
            # TODO
            p=-rot_inv.apply(self["p"]),
            q=rot_inv.as_quat(),
        )

    # TODO FIXME performance
    def __mul__(self, other: "Pose"):
        rot = scipy.spatial.transform.Rotation.from_quat(self["q"])
        rot_other = scipy.spatial.transform.Rotation.from_quat(other["q"])

        return Pose(
            p=self["p"] + rot.apply(other["p"]),
            # TODO this is wrong???
            q=(rot * rot_other).as_quat(),
            # q=other["q"],
        )
    
    # TODO pack/unpack for all other methods!!!!!
    @property
    def angles(self):
        q_packed, ps = einops.pack([self["q"]], "* quat")
        [eulers] = einops.unpack(
            # TODO
            scipy.spatial.transform.Rotation.from_quat(q_packed).as_euler("XYZ"), 
            ps, 
            "* eulers",
        )
        return eulers
    

    # TODO !!!
    def to_matrix(self):
        p = numpy.asarray(self["p"])
        q = numpy.asarray(self["q"])

        # TODO
        q_packed, ps = einops.pack([self["q"]], "* quat")
        R = scipy.spatial.transform.Rotation.from_quat(q_packed).as_matrix()
        [R] = einops.unpack(R, ps, "* out_base in_base",)

        # handle batching
        # if p.ndim == 1:  # single pose
        #     T = np.eye(4)
        #     T[:3, :3] = R
        #     T[:3, 3] = p
        # else:  # batched poses [..., 3] / [..., 4]
        eye = numpy.eye(4)
        shape = p.shape[:-1] + (4, 4)
        T = numpy.broadcast_to(eye, shape).copy()
        T[..., :3, :3] = R
        T[..., :3, 3] = p
        return T


In [4]:
a = Pose.from_matrix(
    numpy.array([
        [[0.0, -1.0, 0.0, 1.0],
        [1.0,  0.0, 0.0, 2.0],
        [0.0,  0.0, 1.0, 3.0],
        [0.0,  0.0, 0.0, 1.0]],
        
        [[1.0, 0.0, 0.0, 4.0],
        [0.0, 1.0, 0.0, 5.0],
        [0.0, 0.0, 1.0, 6.0],
        [0.0, 0.0, 0.0, 1.0]]
    ])    
)

a.to_matrix()


array([[[ 0., -1.,  0.,  1.],
        [ 1.,  0.,  0.,  2.],
        [ 0.,  0.,  1.,  3.],
        [ 0.,  0.,  0.,  1.]],

       [[ 1.,  0.,  0.,  4.],
        [ 0.,  1.,  0.,  5.],
        [ 0.,  0.,  1.,  6.],
        [ 0.,  0.,  0.,  1.]]])

In [5]:
Pose.from_matrix(
    numpy.array([
        [0.0, -1.0, 0.0, 1.0],
        [1.0,  0.0, 0.0, 2.0],
        [0.0,  0.0, 1.0, 3.0],
        [0.0,  0.0, 0.0, 1.0],
    ])
).to_matrix()

array([[ 0., -1.,  0.,  1.],
       [ 1.,  0.,  0.,  2.],
       [ 0.,  0.,  1.,  3.],
       [ 0.,  0.,  0.,  1.]])

In [6]:
# TODO
# Pose().inv()
# Pose(p=[1, 0, 0], q=[0, 0, 0, 1]) * Pose(p=[0, 0, 0], q=[0, 0, 0, 1])
# Pose(p=[0, 0, 0], q=[0, 0, 0, 1]).inv()

In [ ]:
# from robotodo.engines.core.path import Path

from typing import Iterable

# TODO
import bracex
import wcmatch.glob


class PathExpression:
    # TODO expr: "str | PathExpression | list[str | PathExpression]"
    def __init__(self, expr: "str | PathExpression"):
        self._expr = str(expr)

    def __str__(self):
        return self._expr

    # TODO this isnt correct!!!
    def resolve(self, paths: Iterable[str]):
        # TODO cache?
        # TODO brace expansion?
        match = wcmatch.glob.compile(self._expr, limit=0, flags=wcmatch.glob.GLOBSTAR)
        return match.filter(paths)

    # TODO
    def expand(self):
        return bracex.expand(self._expr)


# TODO
PathExpressionLike = str | PathExpression



import functools


# TODO multiple scenes are not supported!!!
class Scene:
    # TODO !!!!!
    def __init__(self, kernel: Kernel):
        # TODO !!!!!
        self._kernel = kernel

    # TODO !!!!!
    @property
    def _stage(self):
        # TODO !!!
        stage = self._kernel.omni.usd.get_context().get_stage()
        if stage is None:
            # TODO !!!!!  Stage opening or closing already in progress so async???
            self._kernel.omni.usd.get_context().new_stage()
            stage = self._kernel.omni.usd.get_context().get_stage()
        # TODO check None
        assert stage is not None
        return stage

    def traverse(self, path: PathExpressionLike | None = None):
        # TODO
        if path is not None:
            raise NotImplementedError("TODO")

        root_prim = (
            self._stage.GetPseudoRoot()
            if path is None else
            # TODO
            self._stage.GetPrimAtPath(self.resolve(path))
        )

        return (
            prim.GetPath().pathString
            for prim in self._kernel.pxr.Usd.PrimRange(root_prim)
        )

    def resolve(self, path: PathExpressionLike):
        return PathExpression(path).resolve(self.traverse())

    # TODO
    def copy(self, path: PathExpressionLike, target_path: PathExpressionLike):
        path = PathExpression(path)
        target_path = PathExpression(target_path)

        # TODO mv
        import isaacsim.core.cloner

        # TODO check if dir
        cloner = isaacsim.core.cloner.Cloner(stage=self._stage)
        source_prim_path = self.resolve(path)
        if len(source_prim_path) != 1:
            raise NotImplementedError("TODO")
        source_prim_path = source_prim_path[0]

        cloner.clone(
            source_prim_path=source_prim_path,
            prim_paths=PathExpression(target_path).expand(),
        )

        # raise NotImplementedError

    def move(self, path: PathExpressionLike, target_path: PathExpressionLike):
        path = PathExpression(path)
        target_path = PathExpression(target_path)

        raise NotImplementedError

    # TODO
    def update(self):
        raise NotImplementedError
    
    # TODO
    @property
    def on_update_physics(self):
        raise NotImplementedError
    
    # TODO
    @property
    def on_update_visuals(self):
        raise NotImplementedError

    # TODO kernel thread
    @functools.cached_property
    def __physics_tensor_view_cache(self):
        try:
            # TODO stage_id !!!!!!
            res = self._kernel.omni.physics.tensors.create_simulation_view("torch")
        except Exception as error:
            # TODO
            raise RuntimeError(
                "Failed to create physics view. "
                f"Does a prim of type `PhysicsScene` exist on the stage?"
                # TODO rm
                # f"Make sure the physics simulation is running: call {self.timeline_play}"
            ) from error
        if not res.is_valid:
            raise RuntimeError(f"Created physics view is invalid: {res}")
        return res

    def _physics_tensor_get_view(self):
        if not self.__physics_tensor_view_cache.is_valid:
            del self.__physics_tensor_view_cache
        return self.__physics_tensor_view_cache


# TODO default scene
# scene = Scene()
# TODO new scene
# scene = engine.add(Scene())


class Entity:
    def __init__(self, path: PathExpressionLike, scene: Scene):
        self._scene = scene
        # TODO
        self._path = PathExpression(path)

    # TODO invalidate!!!!
    @functools.cached_property
    def _isaac_usdgeom_xform_cache(self):
        # TODO Usd.TimeCode.Default()
        cache = self._scene._kernel.pxr.UsdGeom.XformCache()

        def _on_changed(notice, sender):
            # TODO
            cache.Clear()

        # TODO NOTE life cycle
        cache._notice_handler = _on_changed
        # TODO
        cache._notice_token = self._scene._kernel.pxr.Tf.Notice.Register(
            self._scene._kernel.pxr.Usd.Notice.ObjectsChanged, 
            cache._notice_handler, 
            self._scene._stage,
        )

        return cache
    
    # TODO
    # TODO https://docs.omniverse.nvidia.com/dev-guide/latest/programmer_ref/usd/transforms/compute-prim-bounding-box.html
    @functools.cached_property
    def _isaac_usdgeom_bbox_cache(self):
        raise NotImplementedError
        return self._scene._kernel.pxr.UsdGeom.BBoxCache(
            self._scene._kernel.pxr.Usd.TimeCode.Default(),
            [self._scene._kernel.pxr.UsdGeom.Tokens.default_,],
        )

    # TODO FIXME performance thru prim obj caching
    @property
    # TODO invalidate !!!!!
    # @functools.cached_property
    def __isaac_prims(self):
        return [
            self._scene._stage.GetPrimAtPath(p)
            for p in self._scene.resolve(self._path)
        ]
        
    @property
    def pose(self):
        # TODO 
        return Pose.from_matrix(
            numpy.stack([
                numpy.asarray(
                    self._isaac_usdgeom_xform_cache
                    .GetLocalToWorldTransform(prim)                
                ).T # TODO NOTE col-major
                for prim in self.__isaac_prims
            ])            
        )


import enum
import functools

# TODO
import torch


# TODO use kernel thread for everything
# TODO NOTE must be homogenous
class Articulation:
    def __init__(self, root_path: PathExpressionLike, scene: Scene):
        self._scene = scene
        # TODO
        self._root_path = PathExpression(root_path)

    @functools.cached_property
    def __physics_tensor_articulation_view_cache(self):
        try:
            resolved_root_paths = self._scene.resolve(self._root_path)
            self._scene._kernel.omni.physx.get_physx_simulation_interface().flush_changes()
            res = self._scene._physics_tensor_get_view().create_articulation_view(
                resolved_root_paths
            )
            assert res is not None
            assert res.check()
        except Exception as error:
            raise RuntimeError(
                f"Failed to create physics view from root joint paths (are they valid?): {resolved_root_paths}"
            ) from error
        return res

    def _physics_tensor_get_articulation_view(self):
        if not self.__physics_tensor_articulation_view_cache.check():
            del self.__physics_tensor_articulation_view_cache
        return self.__physics_tensor_articulation_view_cache

    # TODO
    @property
    def root_joint_path(self):
        # TODO
        return self._physics_tensor_get_articulation_view().prim_paths

    # TODO

    @property
    def link_paths(self):
        return self._physics_tensor_get_articulation_view().link_paths

    # TODO link_names
    # panda_robot._physics_tensor_get_articulation_view().shared_metatype.link_names

    # TODO
    @property
    def link_poses(self):
        """
        TODO doc

        """

        view = self._physics_tensor_get_articulation_view()
        link_transforms = view.get_link_transforms()

        return Pose(
            p=link_transforms[..., [0, 1, 2]],
            q=link_transforms[..., [3, 4, 5, 6]],
        )

    # TODO rm    
    # @link_poses.setter
    # def link_poses(self, value: Pose):
    #     # TODO
    #     view = self._physics_tensor_get_articulation_view()
        
    #     value_ = torch.broadcast_to(
    #         torch.concat((value["p"], value["q"]), dim=-1), 
    #         size=(view.count, view.max_links, 7),
    #     )
    #     view.set_link_transforms(value_, indices=torch.arange(view.count))

    @property
    def dof_count(self):
        return self._physics_tensor_get_articulation_view().max_dofs

    @property
    def dof_names(self):
        # TODO !!!
        return self._physics_tensor_get_articulation_view().shared_metatype.dof_names

    # TODO mv and standardize
    class DOFType(enum.Enum):
        Rotation = 0
        Translation = 1

    # TODO
    @property
    def dof_types(self):
        view = self._physics_tensor_get_articulation_view()
        return view.get_dof_types()

    @property
    def dof_positions(self):
        view = self._physics_tensor_get_articulation_view()
        dof_positions = view.get_dof_positions()
        return dof_positions

    # TODO maybe async???
    # TODO typing
    # TODO support masking !!!!!!
    @dof_positions.setter
    def dof_positions(self, value):
        view = self._physics_tensor_get_articulation_view()
        value_ = torch.broadcast_to(torch.asarray(value), (view.count, view.max_dofs))
        view.set_dof_positions(value_, indices=torch.arange(view.count))

    @property
    def dof_position_limits(self):
        view = self._physics_tensor_get_articulation_view()
        # TODO
        return view.get_dof_limits()

    @property
    def dof_velocities(self):
        view = self._physics_tensor_get_articulation_view()
        velocities = view.get_dof_velocities()
        return velocities

    @dof_velocities.setter
    def dof_velocities(self, value):
        view = self._physics_tensor_get_articulation_view()
        value_ = torch.broadcast_to(torch.asarray(value), (view.count, view.max_dofs))
        view.set_dof_velocities(value_, indices=torch.arange(view.count))

    @functools.cached_property
    def driver(self):
        return ArticulationDriver(articulation=self)

    @property
    def root_pose(self):
        view = self._physics_tensor_get_articulation_view()
        root_trans = view.get_root_transforms()
        return Pose(
            p=root_trans[..., [0, 1, 2]],
            q=root_trans[..., [3, 4, 5, 6]],
        )


class ArticulationDriver:

    def __init__(self, articulation: Articulation):
        self._articulation = articulation

    def compute_dof_passive_gravity_forces(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        # TODO extra +6 dofs when floating base !!!!!!
        # TODO indices: [*base_6dof, *dof]
        return view.get_gravity_compensation_forces()

    def compute_dof_passive_coriolis_and_centrifugal_forces(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        # TODO extra +6 dofs when floating base !!!!!!
        return view.get_coriolis_and_centrifugal_compensation_forces()

    @property
    def dof_stiffnesses(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        return view.get_dof_stiffnesses()

    @dof_stiffnesses.setter
    def dof_stiffnesses(self, value):
        view = self._articulation._physics_tensor_get_articulation_view()
        value_ = torch.broadcast_to(torch.asarray(value), (view.count, view.max_dofs))
        view.set_dof_stiffnesses(value_, indices=torch.arange(view.count))

    @property
    def dof_dampings(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        return view.get_dof_dampings()
    
    @dof_dampings.setter
    def dof_dampings(self, value):
        view = self._articulation._physics_tensor_get_articulation_view()
        value_ = torch.broadcast_to(torch.asarray(value), (view.count, view.max_dofs))
        view.set_dof_dampings(value_, indices=torch.arange(view.count))
    
    # TODO mv and stdize
    class DriveType(enum.Enum):
        Disabled = 0
        Force = 1
        Acceleration = 2

    @property
    def dof_drive_types(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        return view.get_drive_types()

    @property
    def dof_target_positions(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        return view.get_dof_position_targets()

    @dof_target_positions.setter
    def dof_target_positions(self, value):
        view = self._articulation._physics_tensor_get_articulation_view()
        value_ = torch.broadcast_to(torch.asarray(value), (view.count, view.max_dofs))
        view.set_dof_position_targets(value_, indices=torch.arange(view.count))

    @property
    def dof_target_velocities(self):
        view = self._articulation._physics_tensor_get_articulation_view()
        return view.get_dof_velocity_targets()

    @dof_target_velocities.setter
    def dof_target_velocities(self, value):
        view = self._articulation._physics_tensor_get_articulation_view()
        value_ = torch.broadcast_to(torch.asarray(value), (view.count, view.max_dofs))
        view.set_dof_velocity_targets(value_, indices=torch.arange(view.count))

In [ ]:
kernel.start_app_loop_soon()

[13.404s] [ext: isaacsim.ros2.bridge-4.9.3] startup
2025-09-12T09:13:34Z [13,395ms] [Warning] [isaacsim.ros2.bridge.impl.extension] ROS_DISTRO env var not found, Please source ROS before enabling this extension
[13.424s] Using backup internal ROS2 humble distro
[13.432s] To use the internal libraries included with the extension please set the following environment variables to use with FastDDS (default) or CycloneDDS before starting Isaac Sim:

FastDDS (default):
export ROS_DISTRO=humble
export RMW_IMPLEMENTATION=rmw_fastrtps_cpp
export LD_LIBRARY_PATH=$LD_LIBRARY_PATH:/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/isaacsim/exts/isaacsim.ros2.bridge/humble/lib

OR

CycloneDDS:
export ROS_DISTRO=humble
export RMW_IMPLEMENTATION=rmw_cyclonedds_cpp
export LD_LIBRARY_PATH=$LD_LIBRARY_PATH:/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/isaacsim/exts/isaacsim.ros2.bridge/humble/lib




2025-09-12T09:13:34Z [13,403ms] [Error] [isaacsim.ros2.bridge.impl.extension] ROS2 Bridge startup failed


In [10]:
scene = Scene(kernel=kernel)
list(scene.traverse())


['/',
 '/World',
 '/Environment',
 '/Environment/defaultLight',
 '/Render',
 '/Render/OmniverseKit',
 '/Render/OmniverseKit/HydraTextures',
 '/Render/OmniverseKit/HydraTextures/omni_kit_widget_viewport_ViewportTexture_0',
 '/Render/OmniverseGlobalRenderSettings',
 '/Render/Vars',
 '/Render/Vars/LdrColor',
 '/OmniverseKit_Persp',
 '/OmniverseKit_Front',
 '/OmniverseKit_Top',
 '/OmniverseKit_Right']

In [11]:
# URDFImporter()("https://...", id="/World/SomeRobot")

In [13]:

# TODO
def import_urdf(
    resource: str, 
    prim_path: str | None = None,
    fix_base: bool = True,
):
    import omni

    # TODO
    ext_manager = omni.kit.app.get_app().get_extension_manager()
    if not ext_manager.is_extension_enabled("isaacsim.asset.importer.urdf"):
        ext_manager.set_extension_enabled_immediate("isaacsim.asset.importer.urdf", True)

    # TODO
    is_success, import_config = omni.kit.commands.execute(
        "URDFCreateImportConfig"
    )
    assert is_success

    # import_config.convex_decomp = False  # Disable convex decomposition for simplicity
    import_config.fix_base = fix_base       # Fix the base of the robot to the ground
    import_config.make_default_prim = False  # Make the robot the default prim in the scene
    # import_config.self_collision = False  # Disable self-collision for performance
    # import_config.distance_scale = 1     # Set distance scale for the robot
    # import_config.density = 0.0          # Set density to 0 (use default values)

    # from isaacsim.asset.importer.urdf import _urdf

    # Acquire the URDF extension interface for parsing and importing URDF files
    # urdf_interface = _urdf.acquire_urdf_interface()

    # Configure the settings for importing the URDF file
    # import_config = _urdf.ImportConfig()

    # Retrieve the path of the URDF file from the extension


    # from isaacsim.core.utils.extensions import get_extension_path_from_name
    # extension_path = get_extension_path_from_name("isaacsim.asset.importer.urdf")
    # root_path = extension_path + "/data/urdf/robots/franka_description/robots"
    # file_name = "panda_arm_hand.urdf"
    # Parse the robot's URDF file to generate a robot model
    # urdf_path="{}/{}".format(root_path, file_name),

    is_success, robot_model = omni.kit.commands.execute(
        "URDFParseFile",
        urdf_path=resource,
        import_config=import_config
    )
    assert is_success


    # TODO  check if path already exists
    stage = omni.usd.get_context().get_stage()
    assert stage is not None
    if stage.GetPrimAtPath(prim_path).IsValid():
        raise RuntimeError(f"Path already exists: {prim_path}")


    # Update the joint drive parameters for better stiffness and damping
    # for joint in robot_model.joints:
    #     robot_model.joints[joint].drive.strength = 1047.19751  # High stiffness value
    #     robot_model.joints[joint].drive.damping = 52.35988    # Moderate damping value

    # Import the robot onto the current stage and retrieve its prim path
    is_success, prim_path_temp = omni.kit.commands.execute(
        "URDFImportRobot",
        urdf_robot=robot_model,
        import_config=import_config,
        # get_articulation_root=True,
    )
    assert is_success
    if prim_path is None:
        return prim_path_temp

    is_success, _ = omni.kit.commands.execute(
        "MovePrim",
        path_from=prim_path_temp,
        path_to=prim_path,
    )
    assert is_success

    # TODO getprimatpath
    # return stage.GetPrimAtPath(prim_path)
    return prim_path


import warnings

def import_usd(
    file_path: str,
    prim_path: str,
    prim_type: str = "Xform",
):
    import omni
    import pxr
    from omni.metrics.assembler.core import get_metrics_assembler_interface

    
    # TODO
    stage = omni.usd.get_context().get_stage()
    assert stage is not None


    # Handle units
    sdf_layer = pxr.Sdf.Layer.FindOrOpen(file_path)
    if not sdf_layer:
        raise RuntimeError(f"Could not get Sdf layer for {file_path}")
    
    prim = stage.GetPrimAtPath(prim_path)
    if not prim.IsValid():
        prim = stage.DefinePrim(prim_path, prim_type)

    stage_id = pxr.UsdUtils.StageCache.Get().GetId(stage).ToLongInt()
    ret_val = get_metrics_assembler_interface().check_layers(
        stage.GetRootLayer().identifier, sdf_layer.identifier, stage_id
    )
    if ret_val["ret_val"]:
        try:
            __import__("omni.metrics.assembler.ui")
            payref = pxr.Sdf.Reference(file_path)
            omni.kit.commands.execute("AddReference", stage=stage, prim_path=prim.GetPath(), reference=payref)
        except Exception as exc:
            warnings.warn(
                f"The USD file {file_path} used for a reference does have divergent units, "
                f"please either enable omni.usd.metrics.assembler.ui or convert the file into right units: {exc}"
            )
            success_bool = prim.GetReferences().AddReference(file_path)
            if not success_bool:
                raise FileNotFoundError("The usd file at path {} provided wasn't found".format(file_path))
    else:
        success_bool = prim.GetReferences().AddReference(file_path)
        if not success_bool:
            raise FileNotFoundError("The usd file at path {} provided wasn't found".format(file_path))

    return prim


In [14]:
import isaacsim.asset.importer.urdf

In [15]:
import os

from isaacsim.core.utils.extensions import get_extension_path_from_name


panda_arm_hand_urdf_path = os.path.join(
    get_extension_path_from_name("isaacsim.asset.importer.urdf"),
    "data", "urdf", "robots", "franka_description", "robots", "panda_arm_hand.urdf",
)


In [16]:
import_urdf(
    "todo-curobo-sample-configs/franka/franka_description/franka_panda.urdf", 
    prim_path="/World/PandaFixedBase1",
    fix_base=True,
)

2025-09-12T09:14:28Z [67,338ms] [Warning] [isaacsim.asset.importer.urdf] link ee_link has no body properties (mass, inertia, or collisions) and is being merged into panda_hand
2025-09-12T09:14:28Z [67,338ms] [Warning] [isaacsim.asset.importer.urdf] link panda_hand has no body properties (mass, inertia, or collisions) and is being merged into panda_link8
2025-09-12T09:14:28Z [67,338ms] [Warning] [isaacsim.asset.importer.urdf] link panda_link8 has no body properties (mass, inertia, or collisions) and is being merged into panda_link7
2025-09-12T09:14:28Z [67,338ms] [Warning] [isaacsim.asset.importer.urdf] link right_gripper has no body properties (mass, inertia, or collisions) and is being merged into panda_link7
2025-09-12T09:14:28Z [67,338ms] [Warning] [isaacsim.asset.importer.urdf] link panda_link0 has no body properties (mass, inertia, or collisions) and is being merged into base_link
2025-09-12T09:14:28Z [67,339ms] [Warning] [isaacsim.asset.importer.urdf] Creating Asset in an in-memo

'/World/PandaFixedBase1'

2025-09-12T09:14:29Z [68,017ms] [Warning] [usdrt.hydra.fabric_scene_delegate.plugin] using high frequency span with attrs is disabled
2025-09-12T09:14:29Z [68,017ms] [Warning] [omni.fabric.plugin] getAttributeCount called on non-existent path /World/PandaFixedBase1/panda_rightfinger/visuals/finger
2025-09-12T09:14:29Z [68,017ms] [Warning] [omni.fabric.plugin] getTypes called on non-existent path /World/PandaFixedBase1/panda_rightfinger/visuals/finger


In [17]:
# import_urdf(
#     panda_arm_hand_urdf_path, 
#     prim_path="/World/PandaFixedBase0",
#     fix_base=True,
# )

In [18]:
from isaacsim.core.utils.stage import add_reference_to_stage, get_stage_units
from isaacsim.storage.native import get_assets_root_path

# asset_path = get_assets_root_path() + "/Isaac/Robots/FrankaRobotics/FrankaPanda/franka.usd"
# robot1 = add_reference_to_stage(usd_path=asset_path, prim_path="/World/Franka_1")
mug = add_reference_to_stage(usd_path="https://omniverse-content-production.s3-us-west-2.amazonaws.com/Assets/Isaac/5.0/Isaac/Props/Mugs/SM_Mug_A2.usd", prim_path="/World/Mug")
mug


Usd.Prim(</World/Mug>)

2025-09-12T09:14:51Z [90,624ms] [Warning] [carb] Client gpu.foundation.plugin has acquired [gpu::unstable::IMemoryBudgetManagerFactory v0.1] 100 times. Consider accessing this interface with carb::getCachedInterface() (Performance warning)


In [ ]:
lemon = add_reference_to_stage(
    usd_path="https://omniverse-content-staging.s3.us-west-2.amazonaws.com/Assets/simready_content/common_assets/props/lemon_01/lemon_01.usd",
    prim_path="/World/Lemon",
)
lemon

Usd.Prim(</World/Lemon>)

2025-09-11T09:56:29Z [16,064,010ms] [Warning] [semantics.schema.property.semantics_entry] [semantics.schema.property] Semantics.SemanticsAPI is deprecated, please use SemanticsLabelsAPI instead.
2025-09-11T09:56:31Z [16,066,156ms] [Warning] [semantics.schema.property.semantics_entry] [semantics.schema.property] Semantics.SemanticsAPI is deprecated, please use SemanticsLabelsAPI instead.


In [ ]:
import asyncio


# TODO typing
async def callable_to_aiter(register_fn, loop: asyncio.AbstractEventLoop | None = None):
    queue = asyncio.Queue()
    if loop is None:
        loop = asyncio.get_running_loop()

    def cb(*args, **kwargs):
        loop.call_soon_threadsafe(queue.put_nowait, (args, kwargs))

    with register_fn(cb):
        while True:
            item = await queue.get()
            yield item

# # TODO typing
# def callable_to_afuture(
#     callable_ctx, 
#     loop: asyncio.AbstractEventLoop | None = None,
# ):
#     future = asyncio.Future()
#     if loop is None:
#         loop = asyncio.get_running_loop()
    
#     def cb(*args, **kwargs):
#         loop.call_soon_threadsafe(future.set_result, (args, kwargs))

#     # with callable_ctx(cb): pass
#     pass

In [ ]:
import abc
import asyncio
from typing import Callable, Generic, ParamSpec


_P = ParamSpec("_P")

class BaseCallbackEmitter(Generic[_P], abc.ABC):
    @abc.abstractmethod
    def subscribe(self, callable: Callable[_P, Callable[[], None] | None]):
        ...

    def future(self, loop: asyncio.AbstractEventLoop | None = None):
        future = asyncio.Future(loop=loop)

        def f():
            future.set_result

        self.subscribe
        ...

    def stream(self):
        ...

In [ ]:

# class CallbackEmitter:
#     pass


In [21]:
import contextlib

def create_physics_step_event_stream():
    iface = kernel.omni.physx.get_physx_interface()

    # TODO
    @callable_to_aiter
    @contextlib.contextmanager
    def physics_step_event_stream(cb):
        sub = iface.subscribe_physics_step_events(cb)
        yield
        sub.unsubscribe()

    return physics_step_event_stream

# TODO doc examples
# s = create_physics_step_event_stream()
# await anext(s)


In [22]:
# panda_robot = Articulation("/World/PandaFixedBase0", scene=scene)


In [86]:
panda_robot = Articulation("/World/PandaFixedBase1/root_joint", scene=scene)


In [24]:
panda_robot.dof_count

9

In [ ]:
import os

# TODO NOTE seealso https://curobo.org/notes/07_environment_variables.html
os.environ.setdefault("CUROBO_TORCH_CUDA_GRAPH_RESET", "1")

from curobo.types.robot import RobotConfig
from curobo.geom.types import WorldConfig, Mesh

from curobo.types.math import Pose as CuroboPose
from curobo.types.robot import JointState
from curobo.wrap.reacher.motion_gen import (
    MotionGen,
    MotionGenConfig,
    MotionGenPlanConfig,
    PoseCostMetric,
)




kinematics_fused_cu not found, JIT compiling...
/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/torch/utils/cpp_extension.py:2356: UserWarning: TORCH_CUDA_ARCH_LIST is not set, all archs for visible cards are included for compilation. 
If this is not desired, please set os.environ['TORCH_CUDA_ARCH_LIST'].
  warnings.warn(
geom_cu binary not found, jit compiling...
/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/torch/utils/cpp_extension.py:2356: UserWarning: TORCH_CUDA_ARCH_LIST is not set, all archs for visible cards are included for compilation. 
If this is not desired, please set os.environ['TORCH_CUDA_ARCH_LIST'].
  warnings.warn(
tensor_step_cu not found, jit compiling...
/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/torch/utils/cpp_extension.py:2356: UserWarning: TORCH_CUDA_ARCH_LIST is not set, all archs for visible cards are included for compilation. 
If this is not desired, please set os.environ['TORCH_CUDA_ARCH_LIST'].
  warni

In [26]:
import yaml

with open("todo-curobo-sample-configs/franka/config.yml") as f:
    config_file_content = yaml.load(f, yaml.FullLoader)

import os


prefix = "todo-curobo-sample-configs/franka"


for key in [
    "urdf_path",
    "asset_root_path",
    "collision_spheres",
]:
    config_file_content["robot_cfg"]["kinematics"][key] = os.path.join(
        os.path.abspath(prefix),
        config_file_content["robot_cfg"]["kinematics"][key],
    )

config_file_content

{'robot_cfg': {'kinematics': {'urdf_path': '/home/sysadmin/lab/robotodo/__todo__/todo-curobo-sample-configs/franka/franka_description/franka_panda.urdf',
   'asset_root_path': '/home/sysadmin/lab/robotodo/__todo__/todo-curobo-sample-configs/franka/franka_description',
   'base_link': 'panda_link0',
   'ee_link': 'panda_hand',
   'collision_link_names': ['panda_link0',
    'panda_link1',
    'panda_link2',
    'panda_link3',
    'panda_link4',
    'panda_link5',
    'panda_link6',
    'panda_link7',
    'panda_hand',
    'panda_leftfinger',
    'panda_rightfinger',
    'attached_object'],
   'collision_spheres': '/home/sysadmin/lab/robotodo/__todo__/todo-curobo-sample-configs/franka/franka_mesh.yml',
   'collision_sphere_buffer': 0.004,
   'extra_collision_spheres': {'attached_object': 4},
   'use_global_cumul': True,
   'self_collision_ignore': {'panda_link0': ['panda_link1', 'panda_link2'],
    'panda_link1': ['panda_link2', 'panda_link3', 'panda_link4'],
    'panda_link2': ['panda_li

In [27]:
# from curobo.cuda_robot_model.cuda_robot_model import CudaRobotModelConfig, CudaRobotGeneratorConfig

# config = RobotConfig(
#     kinematics=CudaRobotModelConfig.from_config(
#         CudaRobotGeneratorConfig(
#             base_link="panda_link0",
#             ee_link="panda_link7",
#             urdf_path=panda_arm_hand_urdf_path,
#             collision_spheres=spheres["collision_spheres"],
#             collision_link_names=[
#                 'panda_link0',
#                 'panda_link1',
#                 'panda_link2',
#                 'panda_link3',
#                 'panda_link4',
#                 'panda_link5',
#                 'panda_link6',
#                 'panda_link7',
#             ],
#             collision_sphere_buffer=0.004,
#         )
#     ),
# )

In [28]:
# robot_config = RobotConfig.from_basic(
#     # TODO '/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/isaacsim/exts/isaacsim.asset.importer.urdf/data/urdf/robots/franka_description/robots/panda_arm_hand.urdf'
#     urdf_path=panda_arm_hand_urdf_path,
#     # urdf_path='/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/isaacsim/exts/isaacsim.asset.importer.urdf/data/urdf/robots/franka_description/robots/panda_arm_hand.todo.urdf',
#     base_link="panda_link0",
#     # ee_link="panda_link7",
#     ee_link="panda_link8",
# )

In [29]:
robot_config = RobotConfig.from_dict(config_file_content)

In [30]:
# TODO mv to curobo dev
# # config.kinematics.generator_config.collision_link_names
# robot_config.kinematics.kinematics_parser.get_link_parameters("panda_link7")

# robot_config.kinematics.self_collision_config
# # from curobo.geom.sphere_fit import fit_spheres_to_mesh, SphereFitType

# # fit_spheres_to_mesh(
# #     robot_config.kinematics.kinematics_parser.get_link_mesh("panda_link7").get_trimesh_mesh(),
# #     n_spheres=80,                       # tune per link
# #     surface_sphere_radius=0.005,        # ~5mm inflation
# #     fit_type=SphereFitType.VOXEL_VOLUME_SAMPLE_SURFACE,
# # )
# robot_config.kinematics.cspace

# robot_config.kinematics.kinematics_parser.get_link_mesh("panda_link7").file_path
# robot_config.kinematics.kinematics_parser.get_link_mesh("panda_link7").get_trimesh_mesh()

In [708]:
from curobo.util.torch_utils import is_cuda_graph_available, is_cuda_graph_reset_available

# TODO
motion_gen = MotionGen(
    MotionGenConfig.load_from_robot_config(
        robot_cfg=RobotConfig.from_basic(
            # TODO '/home/sysadmin/lab/robotodo/.conda/lib/python3.11/site-packages/isaacsim/exts/isaacsim.asset.importer.urdf/data/urdf/robots/franka_description/robots/panda_arm_hand.urdf'
            urdf_path=panda_arm_hand_urdf_path,
            base_link="panda_link0",
            ee_link="panda_link7",
            # ee_link="panda_leftfinger",
        ),
        # robot_cfg=robot_config,
        world_model=WorldConfig(
            # TODO
            # mesh=curobo_meshes,
        ),
        # interpolation_dt=1 / 250,
        interpolation_dt=1 / 60,
        # num_trajopt_seeds=1,
        # num_graph_seeds=1,
        # TODO requires %env CUROBO_TORCH_CUDA_GRAPH_RESET=1
        # TODO NOTE seealso https://curobo.org/notes/07_environment_variables.html
        use_cuda_graph=is_cuda_graph_available() and is_cuda_graph_reset_available(),
        # use_cuda_graph=False,
    )
)
motion_gen.warmup()


In [ ]:
dof_positions = panda_robot.dof_positions[..., :-2]
# TODO 
target_pose = panda_robot.root_pose.inv() * Pose(p=[.5, -.4, .5], q=[0, 0, 0, 1]) #.rotated([0, 0, numpy.deg2rad(90)])
# TODO feasibility check
# TODO plan_batch
res = motion_gen.plan_single(
    start_state=JointState.from_position(position=torch.tensor(dof_positions, dtype=torch.float32).cuda()),
    goal_pose=CuroboPose(position=torch.tensor(target_pose["p"], dtype=torch.float32).cuda(), quaternion=torch.tensor(target_pose["q"], dtype=torch.float32).cuda()[..., [3, 0, 1, 2]]), 
    # plan_config=MotionGenPlanConfig(num_graph_seeds=1, enable_graph=False, max_attempts=100),
    plan_config=MotionGenPlanConfig(),
)


# res
import numpy

# TODO
for pos, vel in zip(
    res.interpolated_plan.position,
    res.interpolated_plan.velocity,
):   
    # TODO !!!
    # dof_target_pos = panda_robot.dof_positions
    # dof_target_pos[..., :-2] = pos
    # panda_robot.dof_positions = dof_target_pos

    # dof_target_vel = panda_robot.dof_velocities
    # dof_target_vel[..., :-2] = vel
    # panda_robot.dof_velocities = dof_target_vel    

    # continue


    dof_target_pos = panda_robot.driver.dof_target_positions
    dof_target_pos[..., :-2] = pos
    panda_robot.driver.dof_target_positions = dof_target_pos

    dof_target_vel = panda_robot.driver.dof_target_velocities
    dof_target_vel[..., :-2] = vel
    panda_robot.driver.dof_target_velocities = dof_target_vel    

    # TODO FIXME: use events!@!!!!! upstream: await SomeRef.allclose(0, atol=...).event()
    async for event in create_physics_step_event_stream():
        pos_err = panda_robot.dof_positions - panda_robot.driver.dof_target_positions
        vel_err = panda_robot.dof_velocities - panda_robot.driver.dof_target_velocities
        
        if all([
            numpy.allclose(pos_err[..., :-2], 0, atol=1e-2),
            # numpy.allclose(vel_err, 0, atol=1e-1),
        ]):
            break

    # print("...", pos_err, vel_err)
    


/tmp/ipykernel_3731830/3586029327.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.detach().clone() or sourceTensor.detach().clone().requires_grad_(True), rather than torch.tensor(sourceTensor).
  start_state=JointState.from_position(position=torch.tensor(dof_positions, dtype=torch.float32).cuda()),


2025-09-16T07:16:29Z [338,588,424ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:29Z [338,588,469ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:29Z [338,588,513ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:29Z [338,588,557ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:29Z [338,588,601ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:29Z [338,588,

2025-09-16T07:16:33Z [338,592,705ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:33Z [338,592,752ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:33Z [338,592,797ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:34Z [338,592,843ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:34Z [338,592,886ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:16:34Z [338,592,

In [429]:
# CuroboPose(position=torch.tensor(target_pose["p"], dtype=torch.float32).cuda()[0], quaternion=torch.tensor(target_pose["q"], dtype=torch.float32).cuda()[..., [1, 2, 3, 0]][0])

In [430]:

def _pose_to_curobo_pose(pose: Pose):
    return CuroboPose(
        position=torch.tensor(pose["p"], dtype=torch.float32).cuda(), 
        quaternion=torch.tensor(pose["q"], dtype=torch.float32).cuda()[..., [1, 2, 3, 0]],
    )


In [431]:
# TODO
# motion_gen.plan_grasp(
#     start_state=...,
#     grasp_poses=...,
#     plan_config=MotionGenPlanConfig(),
# )

In [432]:
import trimesh
# TODO
from isaacsim.replicator.grasping.grasping_utils import find_first_mesh_in_hierarchy
from isaacsim.replicator.grasping.sampler_utils import sample_antipodal, usd_mesh_to_trimesh

sample_antipodal?

Signature: sample_antipodal(object_mesh: trimesh.base.Trimesh, **kwargs) -> list[numpy.ndarray]
Docstring:
Sample antipodal grasp poses for a given mesh.

Args:
    object_mesh: A trimesh.Trimesh object to sample grasp poses from.
    **kwargs: Dictionary of parameters:
        num_candidates: Target number of grasp candidates to attempt to sample.
        num_orientations: Number of different orientations to sample per valid grasp axis.
        gripper_maximum_aperture: Maximum width between gripper fingers in meters.
        gripper_standoff_fingertips: Distance from fingertip contact points to the gripper's origin along the negative approach direction.
        gripper_approach_direction: Unit vector [x, y, z] indicating the approach direction in the gripper's local frame.
        grasp_align_axis: Unit vector [x, y, z] indicating the gripper's local axis to align with the physical grasp line.
        orientation_sample_axis: Unit vector [x, y, z] indicating the gripper's local axis 

In [ ]:
# import torch

# finger_pos_limits = panda_robot.dof_position_limits[:, -2:, :]
# finger_aperture = torch.sum(
#     finger_pos_limits[..., 1] - finger_pos_limits[..., 0]
# )
# finger_aperture

tensor(0.0960)

In [35]:
from pxr import Gf, Usd
import omni.usd

def get_prim_pose_omni_from_prim_path(prim_path: str):
    ctx = omni.usd.get_context()
    stage = ctx.get_stage()
    prim = stage.GetPrimAtPath(prim_path)
    if not prim or not prim.IsValid():
        raise ValueError(f"Prim not found or invalid: {prim_path}")

    # World transform matrix (composed)
    world_mat: Gf.Matrix4d = omni.usd.get_world_transform_matrix(prim)

    tf = Gf.Transform(world_mat)
    t = tf.GetTranslation()
    q = tf.GetRotation().GetQuat()
    pos = (float(t[0]), float(t[1]), float(t[2]))
    quat = (*map(float, q.GetImaginary()), float(q.GetReal()))
    return Pose(p=pos, q=quat)

def get_prim_pose_omni(prim: Usd.Prim):

    # World transform matrix (composed)
    world_mat: Gf.Matrix4d = omni.usd.get_world_transform_matrix(prim)

    tf = Gf.Transform(world_mat)
    t = tf.GetTranslation()
    q = tf.GetRotation().GetQuat()
    pos = (float(t[0]), float(t[1]), float(t[2]))
    quat = (*map(float, q.GetImaginary()), float(q.GetReal()))
    return Pose(p=pos, q=quat)

In [ ]:
kernel.start_app_loop_soon()

2025-09-15T06:15:45Z [248,544,384ms] [Warning] [omni.kit.window.property.templates.simple_property_widget] PayloadReferenceWidget.build_items took 0.5772885195910931 seconds
TODO <pxr.Usd.ObjectsChanged object at 0x7f8db061fd80> Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('anon:0x7f9c78011910:World0-session.usda'), pathResolverContext=<invalid repr>)
TODO <pxr.Usd.ObjectsChanged object at 0x7f8db0614b80> Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('anon:0x7f9c78011910:World0-session.usda'), pathResolverContext=<invalid repr>)
TODO <pxr.Usd.ObjectsChanged object at 0x7f8dda6f0fe0> Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('anon:0x7f9c78011910:World0-session.usda'), pathResolverContext=<invalid repr>)
TODO <pxr.Usd.ObjectsChanged object at 0x7f8db0617ba0> Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('a

In [ ]:
# cache = pxr.UsdGeom.XformCache()
# %timeit -n 1000 cache.GetLocalToWorldTransform(mug).Orthonormalize()

660 ns ± 257 ns per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [ ]:
# pxr.UsdGeom.XformCache(...)

ArgumentError: Python argument types in
    XformCache.__init__(XformCache, ellipsis)
did not match C++ signature:
    __init__(_object*, pxrInternal_v0_24__pxrReserved__::UsdTimeCode time)
    __init__(_object*)

In [ ]:
# t = cache.GetLocalToWorldTransform(mug)
# %timeit -n 1000 Pose.from_matrix(numpy.asarray(t).T)

91.9 μs ± 2.61 μs per loop (mean ± std. dev. of 7 runs, 1,000 loops each)


In [736]:
e = Entity("/*", scene=scene)
%timeit -n 100 e.pose

2.51 ms ± 678 μs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [ ]:
scene._stage

Usd.Stage.Open(rootLayer=Sdf.Find('anon:0x7f9c78006660:World0.usd'), sessionLayer=Sdf.Find('anon:0x7f9c78011910:World0-session.usda'), pathResolverContext=<invalid repr>)

In [252]:
Entity("/World/Mug", scene=scene).pose

{'p': array([[-0.55611563,  0.25560042,  0.30051522]]),
 'q': array([[0., 0., 0., 1.]])}

In [36]:
# motion_gen.plan_grasp?

In [37]:
panda_robot.root_pose

{'p': tensor([[ 1.8626e-09,  2.3283e-10, -3.7253e-09]]),
 'q': tensor([[0., 0., 0., 1.]])}

In [38]:
panda_robot.dof_count

9

In [39]:
motion_gen

MotionGen(ik_seeds=32, graph_seeds=4, trajopt_seeds=4, noisy_trajopt_seeds=1, batch_ik_seeds=32, batch_trajopt_seeds=1, robot_cfg=RobotConfig(kinematics=CudaRobotModelConfig(tensor_args=TensorDeviceType(device=device(type='cuda', index=0), dtype=torch.float32, collision_geometry_dtype=torch.float32, collision_gradient_dtype=torch.float32, collision_distance_dtype=torch.float32), link_names=['panda_link7'], kinematics_config=KinematicsTensorConfig(fixed_transforms=tensor([[[ 1.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00],
         [ 0.0000e+00,  1.0000e+00,  0.0000e+00,  0.0000e+00],
         [ 0.0000e+00,  0.0000e+00,  1.0000e+00,  0.0000e+00],
         [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  1.0000e+00]],

        [[ 1.0000e+00,  0.0000e+00,  0.0000e+00,  0.0000e+00],
         [ 0.0000e+00,  1.0000e+00,  0.0000e+00,  0.0000e+00],
         [ 0.0000e+00,  0.0000e+00,  1.0000e+00,  3.3300e-01],
         [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  1.0000e+00]],

        [[ 1.0000e+00,  

In [40]:
from isaacsim.replicator.grasping.ui import grasping_ui_utils

import pxr

# TODO
grasping_ui_utils.clear_debug_draw()
grasping_ui_utils.draw_grasp_samples_as_lines?


Signature:
grasping_ui_utils.draw_grasp_samples_as_lines(
    grasp_poses: list[tuple['Gf.Vec3d', 'Gf.Quatd']],
    point_size: float = 5,
    line_thickness: float = 3,
    line_length: float = 0.02,
    line_opacity: float = 0.5,
    clear_existing: bool = True,
)
Docstring:
Draw grasp samples in the viewport.

Args:
    grasp_poses: List of (Gf.Vec3d, Gf.Quatd) tuples representing position and orientation.
    point_size: Size of the points to draw.
    line_thickness: Thickness of the orientation lines.
    line_length: Length of the orientation lines.
    line_opacity: Opacity of the orientation lines.
    clear_existing: Whether to clear existing samples before drawing.
File:      ~/lab/robotodo/.conda/lib/python3.11/site-packages/isaacsim/exts/isaacsim.replicator.grasping.ui/isaacsim/replicator/grasping/ui/grasping_ui_utils.py
Type:      function

In [41]:
panda_robot.dof_names

['panda_joint1',
 'panda_joint2',
 'panda_joint3',
 'panda_joint4',
 'panda_joint5',
 'panda_joint6',
 'panda_joint7',
 'panda_finger_joint1',
 'panda_finger_joint2']

In [42]:
panda_robot.dof_types

tensor([[0, 0, 0, 0, 0, 0, 0, 1, 1]], dtype=torch.uint8)

In [43]:
motion_gen.robot_cfg.kinematics.get_joint_limits()

JointLimits(joint_names=['panda_joint1', 'panda_joint2', 'panda_joint3', 'panda_joint4', 'panda_joint5', 'panda_joint6', 'panda_joint7'], position=tensor([[-2.8973, -1.7628, -2.8973, -3.0718, -2.8973, -0.0175, -2.8973],
        [ 2.8973,  1.7628,  2.8973, -0.0698,  2.8973,  3.7525,  2.8973]],
       device='cuda:0'), velocity=tensor([[-2.1750, -2.1750, -2.1750, -2.1750, -2.6100, -2.6100, -2.6100],
        [ 2.1750,  2.1750,  2.1750,  2.1750,  2.6100,  2.6100,  2.6100]],
       device='cuda:0'), acceleration=tensor([[-10., -10., -10., -10., -10., -10., -10.],
        [ 10.,  10.,  10.,  10.,  10.,  10.,  10.]], device='cuda:0'), jerk=tensor([[-500., -500., -500., -500., -500., -500., -500.],
        [ 500.,  500.,  500.,  500.,  500.,  500.,  500.]], device='cuda:0'), effort=None, tensor_args=TensorDeviceType(device=device(type='cuda', index=0), dtype=torch.float32, collision_geometry_dtype=torch.float32, collision_gradient_dtype=torch.float32, collision_distance_dtype=torch.float32))

In [97]:
panda_robot.dof_positions

tensor([[-7.1307e-05,  1.3748e-04, -6.4133e-06, -6.9801e-02, -1.4492e-04,
         -1.4611e-03,  8.3154e-06,  3.6508e-04,  4.7046e-09]])

In [ ]:
# get_prim_pose_omni(mesh_prim)

{'p': (-0.5561156288134855, 0.2556004170271337, 0.3005152189592068),
 'q': (0.0, 0.0, 0.0, 1.0)}

In [ ]:

# end_link = ...
# fingertip_link = ...

import numpy as np

# TODO
def standoff_from_poses(T_ee, T_tip, approach_dir_g=np.array([0,0,1]), take_abs=True):
    """
    T_ee: (4,4) EE/TCP pose in world
    T_tips: list of (4,4) fingertip poses in world (one or two)
    approach_dir_g: approach axis in EE frame (e.g., [0,0,1])
    """
    R_ee = T_ee[..., :3, :3]
    p_ee = T_ee[..., :3, 3]
    a_w = R_ee @ (approach_dir_g / np.linalg.norm(approach_dir_g))

    p_tip = T_tip[..., :3, 3]
    return (p_tip - p_ee) @ a_w.T
    # return abs(s) if take_abs else s

# TODO names !!!!
gripper_approach_direction = numpy.array([0, 0, 1])
gripper_standoff_fingertips = standoff_from_poses(
    panda_robot.link_poses._todo_get(..., 7).to_matrix(),
    panda_robot.link_poses._todo_get(..., 8).to_matrix(),
    approach_dir_g=gripper_approach_direction,
)
gripper_standoff_fingertips = numpy.squeeze(
    gripper_standoff_fingertips
)
gripper_standoff_fingertips

In [714]:
panda_robot.dof_position_limits

tensor([[[-2.8973,  2.8973],
         [-1.7628,  1.7628],
         [-2.8973,  2.8973],
         [-3.0718, -0.0698],
         [-2.8973,  2.8973],
         [-0.0175,  3.7525],
         [-2.8973,  2.8973],
         [ 0.0000,  0.0400],
         [ 0.0000,  0.0400]]])

In [729]:
import numpy as np

def _unit(v): 
    v = np.asarray(v, float)
    return v / (np.linalg.norm(v))

def compute_gripper_aperture(T_tipL, T_tipR, T_ee,
                     approach_g=(0,0,1), align_g=(0,1,0)):
    """
    Compute parallel-jaw aperture from two fingertip transforms.
    
    T_tipL, T_tipR, T_ee: 4x4 world transforms
    approach_g: approach axis in EE frame (default z)
    align_g: alignment axis in EE frame (default y)
    """
    R_ee = T_ee[..., :3,:3]
    pL, pR = T_tipL[..., :3,3], T_tipR[..., :3,3]

    # separation axis = cross(approach, align), expressed in world
    sep_w = R_ee @ _unit(np.cross(approach_g, align_g))

    return ((pR - pL) @ sep_w.T)

grasp_align_axis = numpy.array([0, 1, 0])

# TODO NOTE ensure open gripper
gripper_maximum_aperture = compute_gripper_aperture(
    panda_robot.link_poses._todo_get(..., 8).to_matrix(),
    panda_robot.link_poses._todo_get(..., 9).to_matrix(),
    panda_robot.link_poses._todo_get(..., 7).to_matrix(),
    approach_g=gripper_approach_direction,
    align_g=grasp_align_axis,
)
gripper_maximum_aperture = numpy.squeeze(gripper_maximum_aperture)

In [730]:
gripper_standoff_fingertips
gripper_maximum_aperture

array(0.02828436)

In [733]:
# TODO FIXME performance: slow asf! do not use
from curobo.util.usd_helper import UsdHelper

usd_help = UsdHelper()
usd_help.load_stage(scene._stage)
# %prun obstacles = usd_help.get_obstacles_from_stage(ignore_paths=["/World/PandaFixedBase1"])
# TODO
obstacles = usd_help.get_obstacles_from_stage(ignore_paths=["/World/PandaFixedBase1"])


motion_gen.update_world(
    obstacles.get_collision_check_world()
)

Mesh faces 1.3333333333333333 are not matching faceVertexCounts 1
Object already in warp cache, using existing instance for: /World/Mug/SM_Mug_A2
Object already in warp cache, using existing instance for: /visuals/base_link/link0/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link1/link1/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link2/link2/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link3/link3/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link4/link4/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link5/link5/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link6/link6/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link7/link7/mesh
Object already in warp cache, using existing instance for: /visuals/panda_link7/hand/mesh
Object already in warp cache, using ex

In [735]:
import trimesh
# TODO
from isaacsim.replicator.grasping.grasping_utils import find_first_mesh_in_hierarchy
from isaacsim.replicator.grasping.sampler_utils import sample_antipodal, usd_mesh_to_trimesh, transforms_to_vec3d_quatd



dof_positions = panda_robot.dof_positions[..., :-2]

import numpy

# TODO multiple meshes!!!!
mesh_prim = find_first_mesh_in_hierarchy(
    scene._stage.GetPrimAtPath("/World/Mug")
)
grasp_poses = Pose.from_matrix(
    # TODO check if empty
    sample_antipodal(
        usd_mesh_to_trimesh(mesh_prim),
        # num_candidates=2,
        # num_orientations=10,
        # TODO this needs to be measured when open
        # gripper_maximum_aperture=0.1,
        gripper_maximum_aperture=gripper_maximum_aperture,
        # gripper_maximum_aperture=numpy.asarray(finger_aperture),
        # gripper_standoff_fingertips=0.25,
        gripper_standoff_fingertips=gripper_standoff_fingertips,
        # gripper_approach_direction=numpy.array([0, 0, 1]),
        gripper_approach_direction=gripper_approach_direction,
        # TODO
        # grasp_align_axis=numpy.array([0, 1, 0]),
        grasp_align_axis=grasp_align_axis,
        orientation_sample_axis=numpy.array([0, 1, 0]),
    )
)


grasp_poses_global = get_prim_pose_omni(mesh_prim) * grasp_poses
# grasp_poses
# TODO to local frame
# grasp_poses
# TODO
grasping_ui_utils.clear_debug_draw()
# TODO customize: Axis colors: X=Red, Y=Green, Z=Blue
grasping_ui_utils.draw_grasp_samples_as_axes(
    list(zip(*transforms_to_vec3d_quatd(grasp_poses_global.to_matrix()))),
    # axis_length=.1,
    clear_existing=False,
)





grasp_poses_local_to_root = panda_robot.root_pose.inv() * grasp_poses_global


res = motion_gen.plan_grasp(
    start_state=JointState.from_position(
        position=torch.tensor(dof_positions, dtype=torch.float32).cuda(),
    ),
    # TODO FIXME
    grasp_poses=CuroboPose(
        position=torch.tensor([grasp_poses_local_to_root["p"]], dtype=torch.float32).cuda(), 
        quaternion=-torch.tensor([grasp_poses_local_to_root["q"]], dtype=torch.float32).cuda()[..., [3, 0, 1, 2]],
        # quaternion=torch.tensor([grasp_poses_local_to_root["q"]], dtype=torch.float32).cuda(),
    ),
    plan_config=MotionGenPlanConfig(),
    # TODO
    # plan_approach_to_grasp=False,    
    grasp_approach_offset=CuroboPose.from_list([0, 0, 0, 1, 0, 0, 0]),
    # grasp_approach_path_constraint=None,
    # grasp_approach_constraint_in_goal_frame=False,
    # grasp_approach_path_constraint=None,
    # plan_grasp_to_retract=False,
)




res
import numpy



# TODO
for pos, vel in zip(
    res.grasp_interpolated_trajectory.position,
    res.grasp_interpolated_trajectory.velocity,
):   
    # # # # TODO !!!
    dof_target_pos = panda_robot.dof_positions
    dof_target_pos[..., :-2] = pos
    panda_robot.dof_positions = dof_target_pos

    dof_target_vel = panda_robot.dof_velocities
    dof_target_vel[..., :-2] = vel
    panda_robot.dof_velocities = dof_target_vel    

    async for event in create_physics_step_event_stream():
        break

    continue


    dof_target_pos = panda_robot.driver.dof_target_positions
    dof_target_pos[..., :-2] = pos
    panda_robot.driver.dof_target_positions = dof_target_pos

    dof_target_vel = panda_robot.driver.dof_target_velocities
    dof_target_vel[..., :-2] = vel
    panda_robot.driver.dof_target_velocities = dof_target_vel    

    # TODO FIXME: use events!@!!!!! upstream: await SomeRef.allclose(0, atol=...).event()
    async for event in create_physics_step_event_stream():
        pos_err = panda_robot.dof_positions - panda_robot.driver.dof_target_positions
        vel_err = panda_robot.dof_velocities - panda_robot.driver.dof_target_velocities
        
        if all([
            numpy.allclose(pos_err[..., :-2], 0, atol=1e-1),
            # numpy.allclose(vel_err, 0, atol=1e-1),
        ]):
            break

    print("...", pos_err, vel_err)
    


Using mesh '/World/Mug/SM_Mug_A2' under '/World/Mug'.


/tmp/ipykernel_3731830/2802011385.py:60: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.detach().clone() or sourceTensor.detach().clone().requires_grad_(True), rather than torch.tensor(sourceTensor).
  position=torch.tensor(dof_positions, dtype=torch.float32).cuda(),


2025-09-16T07:29:44Z [339,383,206ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:44Z [339,383,260ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:44Z [339,383,316ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:44Z [339,383,369ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:44Z [339,383,423ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:44Z [339,383,

2025-09-16T07:29:47Z [339,386,538ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:47Z [339,386,621ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:47Z [339,386,700ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:47Z [339,386,754ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:47Z [339,386,808ms] [Warning] [omni.usd] Warning: in operator() at line 73 of /builds/omniverse/usd-ci/USD/pxr/base/tf/pyFunction.h -- Tried to call an expired python callback

2025-09-16T07:29:48Z [339,386,

In [567]:
pos_err

tensor([[ 1.9118e-05, -3.5642e-03,  5.7576e-03, -1.1064e-03, -2.2908e-03,
         -4.8990e-03, -2.5392e-05, -1.5024e-04,  1.5287e-04]])

In [ ]:
# panda_robot.driver.dof_target_positions = 0
# panda_robot.driver.dof_target_velocities = 0

# TODO
# panda_robot.driver.dof_dampings = 0
# panda_robot.driver.dof_stiffnesses = 0

In [70]:
panda_robot.link_poses

{'p': tensor([[[ 1.8626e-09,  2.3283e-10, -3.7253e-09],
          [ 1.2107e-08, -5.5879e-09,  3.3300e-01],
          [ 1.4901e-08,  7.4506e-09,  3.3300e-01],
          [-2.1391e-01,  7.3973e-02,  5.5352e-01],
          [-2.5753e-01,  1.1563e-01,  4.9723e-01],
          [-4.0057e-01,  2.8844e-01,  1.7483e-01],
          [-4.0057e-01,  2.8844e-01,  1.7483e-01],
          [-3.3567e-01,  3.1974e-01,  1.2432e-01],
          [-4.3702e-01,  3.5646e-01, -1.5762e-03],
          [-4.4498e-01,  3.5381e-01,  4.9659e-03]]]),
 'q': tensor([[[ 0.0000e+00,  0.0000e+00,  0.0000e+00,  1.0000e+00],
          [ 1.2480e-07, -7.4506e-09,  9.8618e-01,  1.6570e-01],
          [-3.7900e-01, -5.9695e-01,  6.8804e-01, -1.6309e-01],
          [-3.8867e-01,  4.5802e-03,  8.7426e-01,  2.9084e-01],
          [-5.6134e-01,  2.7542e-01, -7.5005e-02,  7.7680e-01],
          [-8.7138e-02,  9.7422e-01,  1.9133e-01, -8.1780e-02],
          [ 7.6331e-01,  3.3298e-01, -1.4263e-01,  5.3492e-01],
          [ 8.2271e-01,  4.28

In [75]:
pos

tensor([ 2.8087,  0.7972, -0.3106, -2.0065,  2.4496,  2.6081, -0.6703],
       device='cuda:0')

In [72]:
pos_err

tensor([[ 0.0006,  0.0012,  0.0019, -0.0010,  0.0013, -0.0017,  0.0003,  0.0046,
          0.0000]])

In [ ]:
# grasp_poses_local_to_root["q"][res.goalset_result.goalset_index]

AttributeError: 'MotionGenResult' object has no attribute 'goalset_result'

In [80]:
grasp_poses_local_to_root["q"][res.goalset_index]

array([-0.2640248 , -0.2640248 ,  0.82231702,  0.42939089])

In [ ]:
grasp_poses_local_to_root["q"][0]

array([8.37814696e-01, 5.45954661e-01, 1.47499247e-04, 1.47499247e-04])

In [82]:
panda_robot.link_poses["q"]#[:, -3]

tensor([[[ 0.0000e+00,  0.0000e+00,  0.0000e+00,  1.0000e+00],
         [ 1.2480e-07, -7.4506e-09,  9.8618e-01,  1.6570e-01],
         [-3.7900e-01, -5.9695e-01,  6.8804e-01, -1.6309e-01],
         [-3.8867e-01,  4.5802e-03,  8.7426e-01,  2.9084e-01],
         [-5.6134e-01,  2.7542e-01, -7.5005e-02,  7.7680e-01],
         [-8.7138e-02,  9.7422e-01,  1.9133e-01, -8.1780e-02],
         [ 7.6331e-01,  3.3298e-01, -1.4263e-01,  5.3492e-01],
         [ 8.2271e-01,  4.2891e-01, -2.6451e-01, -2.6309e-01],
         [ 5.9595e-01,  7.1110e-01, -1.4370e-01, -3.4428e-01],
         [ 5.9595e-01,  7.1110e-01, -1.4370e-01, -3.4428e-01]]])

In [727]:
res.goalset_index

tensor(75, device='cuda:0', dtype=torch.int32)

In [712]:
res.goalset_result.goalset_index

tensor(0, device='cuda:0', dtype=torch.int32)

In [379]:
dof_positions = panda_robot.dof_positions[..., :-2]
# TODO 
# target_pose = panda_robot.root_pose.inv() * Pose(p=[.5, -.4, .5], q=[0, 0, 0, 1])
# TODO plan_batch
res = motion_gen.plan_single(
    start_state=JointState.from_position(position=torch.tensor(dof_positions, dtype=torch.float32).cuda()),
    goal_pose=CuroboPose(position=torch.tensor(grasp_poses_local_to_root["p"], dtype=torch.float32).cuda()[[0]], quaternion=torch.tensor(grasp_poses_local_to_root["q"], dtype=torch.float32).cuda()[..., [1, 2, 3, 0]])[[0]], 
    # plan_config=MotionGenPlanConfig(num_graph_seeds=1, enable_graph=False, max_attempts=100),
    plan_config=MotionGenPlanConfig(),
)


# res
import numpy

# TODO
for pos, vel in zip(
    res.interpolated_plan.position,
    res.interpolated_plan.velocity,
):   
    # # TODO !!!
    # dof_target_pos = panda_robot.dof_positions
    # dof_target_pos[..., :-2] = pos
    # panda_robot.dof_positions = dof_target_pos

    # dof_target_vel = panda_robot.dof_velocities
    # dof_target_vel[..., :-2] = vel
    # panda_robot.dof_velocities = dof_target_vel    

    # await anext(create_physics_step_event_stream())

    # continue


    dof_target_pos = panda_robot.driver.dof_target_positions
    dof_target_pos[..., :-2] = pos
    panda_robot.driver.dof_target_positions = dof_target_pos

    dof_target_vel = panda_robot.driver.dof_target_velocities
    dof_target_vel[..., :-2] = vel
    panda_robot.driver.dof_target_velocities = dof_target_vel    

    # TODO FIXME: use events!@!!!!! upstream: await SomeRef.allclose(0, atol=...).event()
    async for event in create_physics_step_event_stream():
        pos_err = panda_robot.dof_positions - panda_robot.driver.dof_target_positions
        vel_err = panda_robot.dof_velocities - panda_robot.driver.dof_target_velocities
        
        if all([
            numpy.allclose(pos_err[..., :-2], 0, atol=1e-2),
            # numpy.allclose(vel_err, 0, atol=1e-1),
        ]):
            break

    # print("...", pos_err, vel_err)
    


/tmp/ipykernel_3731830/2335086248.py:6: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.detach().clone() or sourceTensor.detach().clone().requires_grad_(True), rather than torch.tensor(sourceTensor).
  start_state=JointState.from_position(position=torch.tensor(dof_positions, dtype=torch.float32).cuda()),


In [559]:
res.goalset_result.goalset_index

tensor(55, device='cuda:0', dtype=torch.int32)

In [562]:
res.goalset_index

tensor(29, device='cuda:0', dtype=torch.int32)

In [573]:
grasping_ui_utils.draw_grasp_samples_as_axes(
    list(zip(*transforms_to_vec3d_quatd(Pose(
        p=grasp_poses_global["p"][[res.goalset_index.cpu()]],
        q=grasp_poses_global["q"][[res.goalset_index.cpu()]],
    )
    .to_matrix())))
)


{'p': array([0.23728392, 0.20579663, 0.71111977]),
 'q': array([0.29638342, 0.29638342, 0.89166167, 0.17103564])}

In [502]:
grasp_poses

{'p': array([[-0.01129483, -0.01195246, -0.07604699],
        [-0.05050727,  0.03245221,  0.10945545],
        [ 0.03659434, -0.00237612, -0.07218019],
        [-0.04162772, -0.03153661, -0.05408676],
        [-0.00092745, -0.00750384,  0.12524358],
        [ 0.09133133,  0.03467219,  0.0008934 ],
        [-0.0033434 , -0.00849503,  0.12638639],
        [-0.0947182 ,  0.01278966,  0.01224867],
        [-0.07882739,  0.01471659,  0.10536159],
        [-0.05157577,  0.01276591,  0.1147338 ],
        [-0.09039931, -0.0300601 ,  0.00506562],
        [-0.02418123,  0.02893112, -0.05505397],
        [-0.01147329, -0.00448989,  0.12819701],
        [ 0.08892982,  0.03299307,  0.04932795],
        [-0.01419302, -0.00705582, -0.06996671],
        [ 0.02341125, -0.01773585, -0.06766843],
        [-0.00392643, -0.00599238,  0.12602013],
        [ 0.02346051, -0.01534077, -0.06865753],
        [-0.04384817,  0.00206658, -0.06037879],
        [ 0.04121543, -0.02465133,  0.10681773],
        [ 0.054

In [453]:
pos_err

tensor([[ 1.4802e-04, -1.0308e-04,  2.3556e-04, -2.4421e-04,  4.3033e-05,
          2.9771e-04, -1.9320e-05, -9.9600e+00,  3.4606e-02]])

2025-09-12T03:42:42Z [80,037,681ms] [Warning] [omni.kit.window.property.templates.simple_property_widget] MaterialBindingWidget.build_items took 0.5948383240029216 seconds
2025-09-12T03:42:44Z [80,039,140ms] [Warning] [semantics.schema.property.semantics_entry] [semantics.schema.property] Semantics.SemanticsAPI is deprecated, please use SemanticsLabelsAPI instead.
2025-09-12T03:43:01Z [80,056,018ms] [Warning] [semantics.schema.property.semantics_entry] [semantics.schema.property] Semantics.SemanticsAPI is deprecated, please use SemanticsLabelsAPI instead.


In [126]:
from isaacsim.replicator.grasping.grasping_manager import GraspingManager



In [127]:
grasping_manager = GraspingManager()

In [136]:
grasping_manager.set_object_prim_path("/World/Mug")

In [137]:
grasping_manager.get_object_prim()

Usd.Prim(</World/Mug>)

In [138]:
grasping_manager.generate_grasp_poses()

Using mesh '/World/Mug/SM_Mug_A2' under '/World/Mug'.


True

In [139]:
grasping_manager.get_grasp_poses()

[(Gf.Vec3d(0.04122487044364101, -0.015524469704880446, 0.2394709556529837),
  Gf.Quatd(0.0009782760137731902, Gf.Vec3d(-0.8117551448068642, -0.5839962935085021, 0.0009782760137731045))),
 (Gf.Vec3d(-0.04302341795673676, 0.00236095541746882, -0.1043942834744563),
  Gf.Quatd(0.7232129439111489, Gf.Vec3d(-0.0009663275175341987, -0.0009663275175340047, 0.690623754429014))),
 (Gf.Vec3d(-0.10686735058493693, 0.02071833333643329, -0.09509699855652487),
  Gf.Quatd(0.8309526395436486, Gf.Vec3d(0.32126544072869867, 0.32126544072869867, 0.32108370251732327))),
 (Gf.Vec3d(0.17352639926130387, 0.007308825329918205, 0.005056149145586946),
  Gf.Quatd(0.4999001866538682, Gf.Vec3d(-0.5099901643343684, -0.4900098356656316, 0.4999001866538682))),
 (Gf.Vec3d(0.1819668476512544, 0.026153062945306477, 0.0018401325949111893),
  Gf.Quatd(0.49286328643277366, Gf.Vec3d(-0.4961130097129879, -0.4961130097129879, 0.5146159189859244))),
 (Gf.Vec3d(-0.1701363816498723, 0.015722437404455898, 0.004428879068867337),
  